In [ ]:
lum_change_dir = '/Bhaltos/ASHWATH/SAR_data_formatted/lum_change'
dnbr_dir = '/Bhaltos/ASHWATH/Dataset/dNBR'

In [52]:
import os
import re
from datetime import datetime, timedelta

# Helper function to parse dates from filenames
def parse_dates_from_filename(filename, pattern, date_format='%Y%m%d'):
    matches = re.findall(pattern, filename)
    if matches:
        date_strings = [date_str for match in matches for date_str in match if date_str]
        return [datetime.strptime(date_str, date_format) for date_str in date_strings]
    return []

# Helper function to parse fire ID from filenames
def parse_fire_id_from_filename(filename, pattern):
    match = re.search(pattern, filename)
    if match:
        return match.group(1)
    return None

# Function to find matching dNBR files for lum_change files
def find_matching_dnbr_files(lum_change_dir, dnbr_dir):
    lum_change_files = os.listdir(lum_change_dir)
    dnbr_files = os.listdir(dnbr_dir)
    
    # Regex patterns to extract dates and fire ID from filenames
    lum_change_pattern = r'_(\d{8})_(\d{8})_'  # Matches two dates in lum_change filenames
    dnbr_pattern = r'_(\d{8}T\d{6})_(\d{8}T\d{6})_'  # Matches two dates in dnbr filenames
    lum_fire_id_pattern = r'^(\d{3,5})_'  # Matches fire ID at the start of the filename (3, 4, or 5 digits)
    dnbr_fire_id_pattern = r'_(\d{3,5})_\d{8}T\d{6}_\d{8}T\d{6}_10m_DNBR\.TIF'  # Matches fire ID before the first date in dnbr filenames (3, 4, or 5 digits)

    # List to store matches
    matches = []

    for lum_file in lum_change_files:
        lum_fire_id = parse_fire_id_from_filename(lum_file, lum_fire_id_pattern)
        lum_dates = parse_dates_from_filename(lum_file, lum_change_pattern, date_format='%Y%m%d')
        
        if len(lum_dates) < 2 or not lum_fire_id:
            print(f"Skipping {lum_file}: could not extract dates or fire ID")
            continue  # Skip files that do not match the expected pattern
        
        closest_match = None
        smallest_date_diff = timedelta(days=9999)  # Large initial value

        for dnbr_file in dnbr_files:
            if not dnbr_file.startswith('S2B'):
                continue  # Skip dNBR files not starting with 'S2B'

            dnbr_fire_id = parse_fire_id_from_filename(dnbr_file, dnbr_fire_id_pattern)
            dnbr_dates = parse_dates_from_filename(dnbr_file, dnbr_pattern, date_format='%Y%m%dT%H%M%S')
            
            if not dnbr_dates:
                print(f"Skipping {dnbr_file}: could not extract dates")
                continue  # Skip if dates are not found

            if dnbr_fire_id != lum_fire_id:
                print(f"Skipping {dnbr_file}: fire ID does not match {lum_fire_id}")
                continue  # Skip if fire IDs do not match
            
            # Find the closest date in dnbr_dates for each lum_date
            for lum_date in lum_dates:
                for dnbr_date in dnbr_dates:
                    date_diff = abs(dnbr_date - lum_date)
                    if date_diff < smallest_date_diff:
                        smallest_date_diff = date_diff
                        closest_match = (lum_file, dnbr_file)

        if closest_match:
            matches.append(closest_match)
        else:
            print(f"No matching dNBR file found for {lum_file}")

    return matches

# Example usage
lum_change_dir = '/Bhaltos/ASHWATH/SAR_data_formatted/lum_change'
dnbr_dir = '/Bhaltos/ASHWATH/Dataset/dNBR'

matches = find_matching_dnbr_files(lum_change_dir, dnbr_dir)
if matches:
    for lum_file, dnbr_file in matches:
        print(f"Lum Change File: {lum_file} -> dNBR File: {dnbr_file}")
else:
    print("No matching dNBR files found for any lum_change files.")


Skipping S2B_L2A_T12VXH_7123_20210714T181919_20210818T181921_10m_DNBR.TIF: fire ID does not match 2282
Skipping S2B_L2A_T12UXG_7123_20210714T181919_20210818T181921_10m_DNBR.TIF: fire ID does not match 2282
Skipping S2B_L2A_T12UXG_7123_20210714T181919_20210816T182919_10m_DNBR.TIF: fire ID does not match 2282
Skipping S2B_L2A_T21LVC_47422_20210620T140059_20210730T140059_10m_DNBR.TIF: fire ID does not match 2282
Skipping S2B_L2A_T21LVC_47422_20210620T140059_20210725T140101_10m_DNBR.TIF: fire ID does not match 2282
Skipping S2B_L2A_T21LVC_47422_20210703T141049_20210730T140059_10m_DNBR.TIF: fire ID does not match 2282
Skipping S2B_L2A_T21LVC_47422_20210703T141049_20210725T140101_10m_DNBR.TIF: fire ID does not match 2282
Skipping S2B_L2A_T10TEK_2614_20200718T184919_20201024T190451_10m_DNBR.TIF: fire ID does not match 2282
Skipping S2B_L2A_T10TEK_2614_20200718T184919_20201031T185531_10m_DNBR.TIF: fire ID does not match 2282
Skipping S2B_L2A_T10TEK_2614_20200728T184919_20201024T190451_10m_DNBR

In [53]:
len(matches)

207

In [56]:
from collections import Counter

# Count occurrences of each fire ID in matches
fire_id_counter = Counter(parse_fire_id_from_filename(lum_file, r'^(\d{3,5})_') for lum_file, _ in matches)

# Print distribution of matches by fire ID
print("Distribution of matches by fire ID:")
for fire_id, count in fire_id_counter.items():
    print(f"Fire ID: {fire_id} -> Matches: {count}")

Distribution of matches by fire ID:
Fire ID: 2282 -> Matches: 8
Fire ID: 2614 -> Matches: 11
Fire ID: 280 -> Matches: 31
Fire ID: 2819 -> Matches: 16
Fire ID: 5532 -> Matches: 32
Fire ID: 5615 -> Matches: 8
Fire ID: 5950 -> Matches: 42
Fire ID: 7123 -> Matches: 27
Fire ID: 7792 -> Matches: 14
Fire ID: 9844 -> Matches: 18


In [54]:
import os
import re

# Helper function to parse fire ID from filenames
def parse_fire_id_from_filename(filename, pattern):
    match = re.search(pattern, filename)
    if match:
        return match.group(1)
    return None

# Function to check for matching fire IDs between lum_change and dNBR files
def check_fire_id_matches(lum_change_dir, dnbr_dir):
    lum_change_files = os.listdir(lum_change_dir)
    dnbr_files = os.listdir(dnbr_dir)
    
    # Regex patterns to extract fire ID from filenames
    lum_fire_id_pattern = r'^(\d{3,5})_'  # Matches fire ID at the start of the filename (3, 4, or 5 digits)
    dnbr_fire_id_pattern = r'_(\d{3,5})_\d{8}T\d{6}_\d{8}T\d{6}_10m_DNBR\.TIF'  # Matches fire ID before the first date in dnbr filenames (3, 4, or 5 digits)

    # Dictionary to store whether each lum_change file has a matching dNBR file
    lum_change_match_status = {}

    for lum_file in lum_change_files:
        lum_fire_id = parse_fire_id_from_filename(lum_file, lum_fire_id_pattern)
        
        if not lum_fire_id:
            lum_change_match_status[lum_file] = "No fire ID found"
            continue  # Skip files that do not match the expected pattern
        
        match_found = False
        for dnbr_file in dnbr_files:
            if not dnbr_file.startswith('S2B'):
                continue  # Skip dNBR files not starting with 'S2B'

            dnbr_fire_id = parse_fire_id_from_filename(dnbr_file, dnbr_fire_id_pattern)
            if dnbr_fire_id == lum_fire_id:
                match_found = True
                break
        
        if match_found:
            lum_change_match_status[lum_file] = "Match found"
        else:
            lum_change_match_status[lum_file] = "No matching dNBR file with matching fire ID"
    
    return lum_change_match_status

# Example usage
lum_change_dir = '/Bhaltos/ASHWATH/SAR_data_formatted/lum_change'
dnbr_dir = '/Bhaltos/ASHWATH/Dataset/dNBR'

match_status = check_fire_id_matches(lum_change_dir, dnbr_dir)
for lum_file, status in match_status.items():
    print(f"Lum Change File: {lum_file} -> Status: {status}")


Lum Change File: 2282_20200508_20200520_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2282_20200520_20200601_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2282_20200601_20200613_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2282_20200613_20200625_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2282_20200625_20200707_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2282_20200707_20200719_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2282_20200719_20200731_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2282_20200731_20200812_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2614_20200713_20200725_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2614_20200725_20200806_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2614_20200806_20200818_DeltaLumin_100m.tif -> Status: Match found
Lum Change File: 2614_20200818_20200830_DeltaLumin_100m.tif -> Status: Match found
Lum 

In [121]:
import os
import re
import csv
from datetime import datetime, timedelta

# Helper function to parse dates from filenames
def parse_dates_from_filename(filename, pattern, date_format='%Y%m%d'):
    matches = re.findall(pattern, filename)
    if matches:
        date_strings = [date_str for match in matches for date_str in match if date_str]
        return [datetime.strptime(date_str, date_format) for date_str in date_strings]
    return []

# Helper function to parse fire ID from filenames
def parse_fire_id_from_filename(filename, pattern):
    match = re.search(pattern, filename)
    if match:
        return match.group(1)
    return None

# Function to find matching files
def find_matching_files(lum_change_dir, binary_product_dir, coh_change_dir, dnbr_dir, date_tolerance=21):
    date_tolerance = timedelta(days=date_tolerance)
    
    lum_change_files = os.listdir(lum_change_dir)
    binary_product_files = os.listdir(binary_product_dir)
    coh_change_files = os.listdir(coh_change_dir)
    dnbr_files = os.listdir(dnbr_dir)
    
    # Regex patterns to extract dates and fire ID from filenames
    lum_change_pattern = r'_(\d{8})_(\d{8})_'  # Matches two dates in lum_change filenames
    binary_product_pattern = r'_(\d{8})_(\d{8})\.tif'  # Matches two dates in binary_product filenames
    coh_change_pattern = r'_(\d{8})_(\d{8})_(\d{8})'  # Matches three dates in coh_change filenames
    dnbr_pattern = r'_(\d{8}T\d{6})_(\d{8}T\d{6})_'  # Matches two dates in dnbr filenames
    lum_fire_id_pattern = r'^(\d{3,5})_'  # Matches fire ID at the start of the filename (3, 4, or 5 digits)
    dnbr_fire_id_pattern = r'_(\d{3,5})_\d{8}T\d{6}_\d{8}T\d{6}_10m_DNBR\.TIF'  # Matches fire ID before the first date in dnbr filenames (3, 4, or 5 digits)
    binary_product_fire_id_pattern = r'^(\d{3,5})_'  # Matches fire ID in binary_product filenames
    coh_change_fire_id_pattern = r'^(\d{3,5})_'  # Matches fire ID in coh_change filenames

    # Dictionary to store matches
    matches = []
    no_match_reasons = {}

    for lum_file in lum_change_files:
        lum_fire_id = parse_fire_id_from_filename(lum_file, lum_fire_id_pattern)
        lum_dates = parse_dates_from_filename(lum_file, lum_change_pattern, date_format='%Y%m%d')
        
        if len(lum_dates) < 2 or not lum_fire_id:
            no_match_reasons[lum_file] = "Couldn't extract fire ID or not enough dates"
            continue  # Skip files that do not match the expected pattern
        
        # Finding the closest match for dNBR files
        closest_dnbr_file = None
        closest_dnbr_date_diff = timedelta(days=9999)
        
        for dnbr_file in dnbr_files:
            if not dnbr_file.startswith('S2B'):
                continue  # Skip dNBR files not starting with 'S2B'

            dnbr_fire_id = parse_fire_id_from_filename(dnbr_file, dnbr_fire_id_pattern)
            dnbr_dates = parse_dates_from_filename(dnbr_file, dnbr_pattern, date_format='%Y%m%dT%H%M%S')
            
            if dnbr_fire_id != lum_fire_id:
                continue  # Skip if fire IDs do not match
            
            for dnbr_date in dnbr_dates:
                for lum_date in lum_dates:
                    if abs(dnbr_date - lum_date) < closest_dnbr_date_diff:
                        closest_dnbr_date_diff = abs(dnbr_date - lum_date)
                        closest_dnbr_file = dnbr_file

        if not closest_dnbr_file:
            no_match_reasons[lum_file] = "Couldn't find a matching dNBR file"
            closest_dnbr_file = "None"

        # Finding exact matches for binary_product and coh_change files
        binary_product_match = None
        coh_change_match = None
        
        for binary_file in binary_product_files:
            binary_fire_id = parse_fire_id_from_filename(binary_file, binary_product_fire_id_pattern)
            binary_dates = parse_dates_from_filename(binary_file, binary_product_pattern, date_format='%Y%m%d')
            
            if binary_fire_id == lum_fire_id and len(binary_dates) == 2:
                if all(lum_date in binary_dates for lum_date in lum_dates):
                    binary_product_match = binary_file
                    break
        
        if not binary_product_match:
            no_match_reasons[lum_file] = "Couldn't find a matching binary_product file"
            binary_product_match = "None"

        for coh_file in coh_change_files:
            coh_fire_id = parse_fire_id_from_filename(coh_file, coh_change_fire_id_pattern)
            coh_dates = parse_dates_from_filename(coh_file, coh_change_pattern, date_format='%Y%m%d')
            
            if coh_fire_id == lum_fire_id:
                if sum(1 for lum_date in lum_dates if any(coh_date.date() == lum_date.date() for coh_date in coh_dates)) >= 2:
                    coh_change_match = coh_file
                    break
        
        if not coh_change_match:
            no_match_reasons[lum_file] = "Couldn't find an exact matching coh_change file. Found closest match instead."
            closest_coh_file = "None"
        else:
            closest_coh_file = coh_change_match

        # Find closest files for unmatched cases

        if not binary_product_match or not coh_change_match:
            if not binary_product_match:
                binary_product_match = find_closest_file(lum_dates, binary_product_files, binary_product_fire_id_pattern, binary_product_pattern, lum_fire_id)
            if not coh_change_match:
                coh_change_match = find_closest_file(lum_dates, coh_change_files, coh_change_fire_id_pattern, coh_change_pattern, lum_fire_id)
            
        matches.append({
            'lum_change': os.path.join(lum_change_dir, lum_file),
            'coh_change': os.path.join(coh_change_dir, coh_change_match),
            'dnbr': os.path.join(dnbr_dir, closest_dnbr_file),
            'binary_product': os.path.join(binary_product_dir, binary_product_match)
        })
    
    return matches, no_match_reasons

def find_closest_file(lum_dates, file_list, fire_id_pattern, date_pattern, lum_fire_id):
    closest_file = None
    closest_date_diff = timedelta(days=9999)
    
    for file in file_list:
        fire_id = parse_fire_id_from_filename(file, fire_id_pattern)
        dates = parse_dates_from_filename(file, date_pattern, date_format='%Y%m%d' if 'T' not in date_pattern else '%Y%m%dT%H%M%S')
        
        if fire_id != lum_fire_id:
            continue
        
        for date in dates:
            for lum_date in lum_dates:
                if abs(date - lum_date) < closest_date_diff:
                    closest_date_diff = abs(date - lum_date)
                    closest_file = file
    
    return closest_file or "None"

# Example usage
lum_change_dir = '/Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_change'
binary_product_dir = '/Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_products'
coh_change_dir = '/Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_change'
dnbr_dir = '/Bhaltos/ASHWATH/Dataset/dNBR'
csv_file_path = '/Bhaltos/ASHWATH/metadata.csv'

# Find matching files
matches, no_match_reasons = find_matching_files(lum_change_dir, binary_product_dir, coh_change_dir, dnbr_dir)

# Write matches to CSV
with open(csv_file_path, mode='w', newline='') as file:
    writer = csv.DictWriter(file, fieldnames=['lum_change', 'coh_change', 'dnbr', 'binary_product'])
    writer.writeheader()
    for match in matches:
        writer.writerow(match)

# Print reasons for no matches
for lum_file, reason in no_match_reasons.items():
    print(f"Lum Change File: {lum_file} - Reason: {reason}")


Lum Change File: 5532_20200901_20200913_DeltaLumin_100m.tif - Reason: Couldn't find an exact matching coh_change file. Found closest match instead.
Lum Change File: 5532_20200913_20200925_DeltaLumin_100m.tif - Reason: Couldn't find an exact matching coh_change file. Found closest match instead.
Lum Change File: 5532_20200925_20201007_DeltaLumin_100m.tif - Reason: Couldn't find an exact matching coh_change file. Found closest match instead.
Lum Change File: 5532_20201007_20201019_DeltaLumin_100m.tif - Reason: Couldn't find an exact matching coh_change file. Found closest match instead.
Lum Change File: 5532_20201019_20201031_DeltaLumin_100m.tif - Reason: Couldn't find an exact matching coh_change file. Found closest match instead.
Lum Change File: 5532_20201031_20201112_DeltaLumin_100m.tif - Reason: Couldn't find an exact matching coh_change file. Found closest match instead.
Lum Change File: 5532_20201112_20201124_DeltaLumin_100m.tif - Reason: Couldn't find an exact matching coh_change

In [122]:
len(matches)

207

In [123]:
import pandas as pd

df = pd.read_csv('/Bhaltos/ASHWATH/metadata.csv')

df.head()

lum_change   
0  /Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_cha...  \
1  /Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_cha...   
2  /Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_cha...   
3  /Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_cha...   
4  /Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_cha...   

                                          coh_change   
0  /Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_cha...  \
1  /Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_cha...   
2  /Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_cha...   
3  /Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_cha...   
4  /Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_cha...   

                                                dnbr   
0  /Bhaltos/ASHWATH/Dataset/dNBR/S2B_L2A_T12SVC_2...  \
1  /Bhaltos/ASHWATH/Dataset/dNBR/S2B_L2A_T12SVC_2...   
2  /Bhaltos/ASHWATH/Dataset/dNBR/S2B_L2A_T12SVC_2...   
3  /Bhaltos/ASHWATH/Dataset/dNBR/S2B_L2A_T12SVC_2...   
4  /Bhaltos/ASHWATH/Dataset/dNBR/S2B_L2A_T12SVC_2...   

                                      binary_product  
0  /Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_...  
1  /Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_...  
2  /Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_...  
3  /Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_...  
4  /Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_...

In [125]:
import pandas as pd
import shutil
import os
import rasterio
from rasterio.enums import Resampling
from rasterio.warp import calculate_default_transform, reproject

# File paths
metadata_csv_path = '/Bhaltos/ASHWATH/metadata.csv'
destination_dir = '/Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr'
metadata_v2_csv_path = '/Bhaltos/ASHWATH/metadata_v2.csv'

# Ensure the destination directory exists
os.makedirs(destination_dir, exist_ok=True)

# Read the metadata CSV
df = pd.read_csv(metadata_csv_path)

# List to hold updated paths
updated_paths = []

# Process each row in the CSV
for index, row in df.iterrows():
    dnbr_file = row['dnbr']
    
    # Ensure the dnbr file path is not NaN
    if pd.notna(dnbr_file):
        # Copy the dNBR file to the destination directory
        shutil.copy(dnbr_file, destination_dir)
        
        # Resample the copied file to 100m resolution
        src_path = os.path.join(destination_dir, os.path.basename(dnbr_file))
        
        # Create a new filename by replacing _10m with _100m
        base_name = os.path.basename(dnbr_file)
        new_base_name = base_name.replace('_10m', '_100m')
        dst_path = os.path.join(destination_dir, new_base_name)
        
        with rasterio.open(src_path) as src:
            # Get the current resolution
            src_transform = src.transform
            src_crs = src.crs
            src_width, src_height = src.width, src.height
            
            # Target dimensions
            target_width = 1098
            target_height = 1098
            
            # Calculate transform and dimensions for the target resolution
            transform, width, height = calculate_default_transform(
                src.crs, src.crs, src_width, src_height, 
                *src.bounds, dst_width=target_width, dst_height=target_height
            )
            
            # Reproject and resample the data
            with rasterio.open(dst_path, 'w', driver='GTiff',
                               height=height, width=width,
                               count=src.count, dtype=src.dtypes[0],
                               crs=src.crs, transform=transform) as dst:
                for i in range(1, src.count + 1):
                    reproject(
                        source=rasterio.band(src, i),
                        destination=rasterio.band(dst, i),
                        src_transform=src_transform,
                        src_crs=src.crs,
                        dst_transform=transform,
                        dst_crs=src.crs,
                        resampling=Resampling.bilinear
                    )
        
        # Update the path in the DataFrame
        updated_paths.append(dst_path)
    else:
        updated_paths.append(dnbr_file)  # If no valid dNBR file path, keep original

# Update the 'dnbr' column in the DataFrame
df['dnbr'] = updated_paths

# Save the updated DataFrame to a new CSV file
df.to_csv(metadata_v2_csv_path, index=False)

print("Processing and CSV update complete.")

Processing and CSV update complete.


In [126]:
df = pd.read_csv('/Bhaltos/ASHWATH/metadata_v2.csv')

df.head()

lum_change   
0  /Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_cha...  \
1  /Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_cha...   
2  /Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_cha...   
3  /Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_cha...   
4  /Bhaltos/ASHWATH/SAR_data_formatted_v2/lum_cha...   

                                          coh_change   
0  /Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_cha...  \
1  /Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_cha...   
2  /Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_cha...   
3  /Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_cha...   
4  /Bhaltos/ASHWATH/SAR_data_formatted_v2/coh_cha...   

                                                dnbr   
0  /Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2...  \
1  /Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2...   
2  /Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2...   
3  /Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2...   
4  /Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2...   

                                      binary_product  
0  /Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_...  
1  /Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_...  
2  /Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_...  
3  /Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_...  
4  /Bhaltos/ASHWATH/SAR_data_formatted_v2/binary_...

In [127]:
df = pd.read_csv('/Bhaltos/ASHWATH/metadata_v2.csv')

df['dnbr'].value_counts()

dnbr
/Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2B_L2A_T12VXH_7123_20210714T181919_20210818T181921_100m_DNBR.TIF    23
/Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2B_L2A_T19LFF_5532_20201005T143729_20201122T144731_100m_DNBR.TIF    18
/Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2B_L2A_T10SFJ_5950_20210720T183919_20211001T185119_100m_DNBR.TIF    13
/Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2B_L2A_T19NBD_9844_20210115T151709_20210321T151701_100m_DNBR.TIF    12
/Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2B_L2A_T16PHC_2819_20190424T155829_20190603T155829_100m_DNBR.TIF    12
/Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2B_L2A_T10SGJ_5950_20210723T184919_20211003T184221_100m_DNBR.TIF    10
/Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2B_L2A_T12VUH_280_20190418T185919_20190528T185929_100m_DNBR.TIF      8
/Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2B_L2A_T12VUH_280_20190418T185919_20190617T185929_100m_DNBR.TIF      8
/Bhaltos/ASHWATH/SAR_data_formatted_v2/dnbr/S2B_L2A_T12VUH_280_2019

In [128]:
import pandas as pd
import rasterio

# Load the metadata CSV into a DataFrame
metadata_v2_path = '/Bhaltos/ASHWATH/metadata_v2.csv'
df = pd.read_csv(metadata_v2_path)

# Get the first row of the DataFrame
first_row = df.iloc[0]

# Extract file paths from the first row
lum_change_path = first_row['lum_change']
coh_change_path = first_row['coh_change']
dnbr_path = first_row['dnbr']
binary_product_path = first_row['binary_product']

# Function to read a GeoTIFF and return its shape
def get_geotiff_shape(file_path):
    with rasterio.open(file_path) as src:
        return src.shape

# Get shapes for each file
lum_change_shape = get_geotiff_shape(lum_change_path)
coh_change_shape = get_geotiff_shape(coh_change_path)
dnbr_shape = get_geotiff_shape(dnbr_path)
binary_product_shape = get_geotiff_shape(binary_product_path)

# Print the shapes
print(f"Lum Change Shape: {lum_change_shape}")
print(f"Coh Change Shape: {coh_change_shape}")
print(f"dNBR Shape: {dnbr_shape}")
print(f"Binary Product Shape: {binary_product_shape}")


Lum Change Shape: (983, 918)
Coh Change Shape: (983, 918)
dNBR Shape: (983, 918)
Binary Product Shape: (983, 918)
